In [1]:
from keras.layers import GlobalMaxPooling2D
from keras.applications.resnet50 import ResNet50,preprocess_input

In [2]:
conv_layer=ResNet50(weights='imagenet', include_top=False, input_shape=(224,224,3))
conv_layer.trainable=False

In [3]:
from keras import Sequential

model=Sequential()
model.add(conv_layer)
model.add(GlobalMaxPooling2D())
model.summary()

Model: "sequential"

┏━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━━━━━━━━━━┳━━━━━━━━━━━━━━━┓
┃ Layer (type)                    ┃ Output Shape           ┃       Param # ┃
┡━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━━━━━━━━━━╇━━━━━━━━━━━━━━━┩
│ resnet50 (Functional)           │ ?                      │    23,587,712 │
├─────────────────────────────────┼────────────────────────┼───────────────┤
│ global_max_pooling2d            │ ?                      │   0 (unbuilt) │
│ (GlobalMaxPooling2D)            │                        │               │
└─────────────────────────────────┴────────────────────────┴───────────────┘

 Total params: 23,587,712 (89.98 MB)

 Trainable params: 0 (0.00 B)

 Non-trainable params: 23,587,712 (89.98 MB)

In [4]:
import cv2
import numpy as np
import os

In [5]:
def extract_image_features(image_path):
    image=cv2.imread(image_path)
    image=cv2.resize(image, (224, 224))
    image_array=np.array(image)
    image_array=np.expand_dims(image_array, axis=0)
    image_array=preprocess_input(image_array)
    features=model.predict(image_array)
    return features/np.linalg.norm(features)

**Feature Creation**

In [6]:
extract_image_features(r'images\1164.jpg').shape

1/1 ━━━━━━━━━━━━━━━━━━━━ 1s 1s/step


(1, 2048)

In [7]:
features_array=[]

for file in os.listdir(r'images'):
    image_path=os.path.join(r'images',file)
    features_array.append(extract_image_features(image_path))

features_array=np.array(features_array)

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 112ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 46ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 44ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 50ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 48ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 45ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 47ms/step
1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 43ms/step
1/1 ━━━━━━━

In [10]:
features_array.shape

(44441, 1, 2048)

In [12]:
from sklearn.metrics.pairwise import cosine_similarity

features_array=features_array.reshape((44441,2048))
similarity_matrix=cosine_similarity(features_array)
similarity_matrix.shape

(44441, 44441)

In [23]:
filenames=[]
from tqdm import tqdm

for file in tqdm(os.listdir(r'images')):
    image_path=os.path.join(r'images',file)
    filenames.append(image_path)

100%|██████████| 44441/44441 [00:00<00:00, 923229.26it/s]


In [26]:
import pickle 
pickle.dump(filenames,open('filenames.pkl','wb'))
# pickle.dump(similarity_matrix, open('similarity_matrix.pkl','wb'))
pickle.dump(features_array, open('features_array.pkl','wb'))

**Recommendation**

In [27]:
from sklearn.neighbors import NearestNeighbors
neighbors=NearestNeighbors(n_neighbors=6, algorithm='brute', metric='euclidean')
neighbors.fit(features_array)

NearestNeighbors(algorithm='brute', metric='euclidean', n_neighbors=6)

In [40]:
def get_recommendation(image_path):
    image_features=extract_image_features(image_path)
    distances, indices= neighbors.kneighbors(image_features)
    return distances, indices[0]

In [41]:
_, indices = get_recommendation(r'images\1531.jpg')

1/1 ━━━━━━━━━━━━━━━━━━━━ 0s 57ms/step


In [42]:
for i in indices:
    print(filenames[i])

images\1531.jpg
images\1539.jpg
images\1886.jpg
images\1562.jpg
images\1563.jpg
images\2056.jpg
